# Structure de données : les dictionnaires

Nous allons manipuler les dictionnaires à partir de fichier (geo)json et cartographier leurs données grâce à la librairie python [Folium](https://python-visualization.github.io/folium/). Folium permet d'utiliser des cartes [Leaflet](https://leafletjs.com) via python.

## Folium

In [2]:
import folium
import requests, json
import urllib.parse
import pandas

In [3]:
grenoble = folium.Map(location = [45.188529, 5.724524], zoom_start = 12)
grenoble

In [4]:
geo = json.load(open("metro/arrets_smtc.geojson"))

*open()* ouvre le fichier et *load* le "parse" en un dictionnaire appelé geo. On accède aux différentes données via une clé (ici *features*) qui renvoit un tableau dont chaque éléement est lui-même un dictionnaire :

In [5]:
geo["features"][0]

{'type': 'Feature',
 'properties': {'id': 'C38:GEN04001',
  'code': 'C38_GEN04001',
  'libelle': 'GARE S.N.C.F',
  'commune': 'GAP',
  'arr_visible': '1',
  'type': 'arret',
  'lametro': False,
  'legresivaudan': False,
  'paysvoironnais': False},
 'geometry': {'type': 'Point', 'coordinates': [6.08569, 44.5636]}}

In [6]:
geo["features"][0]["properties"]["libelle"]

'GARE S.N.C.F'

In [7]:
geo["features"][0]["geometry"]

{'type': 'Point', 'coordinates': [6.08569, 44.5636]}

In [8]:
from folium.plugins import MarkerCluster

grenoble_arret = folium.Map(location = [45.188529, 5.724524], zoom_start = 15)
marker_cluster = MarkerCluster(name = "Arrêts").add_to(grenoble_arret)

for arret in geo["features"]:
    properties = arret["properties"]
    #print(properties["libelle"])
    coordinates = arret["geometry"]["coordinates"]
    coordinates.reverse()
    #print(coordinates)
    folium.Marker(coordinates, popup = properties["libelle"]).add_to(marker_cluster)

In [9]:
grenoble_arret

In [10]:
folium.GeoJson(
    data="metro/limites_communales_metro_epgs4326.geojson",
    name="Limites communales"
).add_to(grenoble_arret)

folium.LayerControl().add_to(grenoble_arret)

In [11]:
grenoble_arret

In [12]:
limites_communales = json.load(open("metro/limites_communales_metro_epgs4326.geojson"))

In [13]:
limites_communales["features"][0]["properties"]

{'code_insee': '38057',
 'nom': 'Bresson',
 'trigram': 'BRE',
 'code_postal': '38320'}

In [14]:
for commune in limites_communales["features"]:
    print(commune["properties"]["nom"])

Bresson
Brié-et-Angonnes
Champagnier
Champ-sur-Drac
Claix
Corenc
Échirolles
Eybens
Fontaine
Le Fontanil-Cornillon
Gières
Jarrie
Meylan
Miribel-Lanchâtre
Le Gua
Herbeys
Grenoble
Montchaboud
Mont-Saint-Martin
Murianette
Notre-Dame-de-Commiers
Notre-Dame-de-Mésage
Noyarey
Poisat
Le Pont-de-Claix
Proveysieux
Quaix-en-Chartreuse
Saint-Barthélemy-de-Séchilienne
Saint-Égrève
Saint-Georges-de-Commiers
Saint-Martin-le-Vinoux
Saint-Paul-de-Varces
Saint-Martin-d'Hères
Saint-Pierre-de-Mésage
Le Sappey-en-Chartreuse
Sarcenas
Sassenage
Séchilienne
Seyssins
La Tronche
Varces-Allières-et-Risset
Seyssinet-Pariset
Vaulnaveys-le-Bas
Vaulnaveys-le-Haut
Veurey-Voroize
Vif
Vizille
Domène
Venon


## Géocodage

Nous allons à présent géocoder des adresses en utilisant le site national des adresses (via son API REST). Les données renvoyées sont au format json.

In [15]:
api_url = "https://api-adresse.data.gouv.fr/search/?q="
adr = "14 avenue Marie Reynoard, 38100 Grenoble"
r = requests.get(api_url + urllib.parse.quote(adr))

print(r.content.decode('unicode_escape'))

{"type": "FeatureCollection", "version": "draft", "features": [{"type": "Feature", "geometry": {"type": "Point", "coordinates": [5.728135, 45.165512]}, "properties": {"label": "14 Avenue Marie Reynoard 38100 Grenoble", "score": 0.9766445454545454, "housenumber": "14", "id": "38185_4853_00014", "name": "14 Avenue Marie Reynoard", "postcode": "38100", "citycode": "38185", "x": 914297.59, "y": 6455503.49, "city": "Grenoble", "context": "38, Isère, Auvergne-Rhône-Alpes", "type": "housenumber", "importance": 0.74309, "street": "Avenue Marie Reynoard"}}], "attribution": "BAN", "licence": "ETALAB-2.0", "query": "14 avenue Marie Reynoard, 38100 Grenoble", "limit": 5}


In [16]:
iuga = json.loads(r.content.decode('unicode_escape'))

In [17]:
iuga["features"][0]["geometry"]["coordinates"].reverse()
iuga_coordinates = iuga["features"][0]["geometry"]["coordinates"]
print(iuga_coordinates)

[45.165512, 5.728135]


In [18]:
iuga_map = folium.Map(iuga_coordinates, zoom_start = 17)
folium.Marker(iuga_coordinates, popup = "IUGA").add_to(iuga_map)

In [19]:
iuga_map